## Dopasowanie par sekwencji. Algorytm kropkowy.


In [1]:
import numpy as np
import matplotlib.pyplot as plt
import os
import re
import requests as r
from io import StringIO
from Bio import SeqIO
import plotly.express as px
import plotly.io as pio

### Wczytanie pliku w formacie Fasta.

In [2]:
def open_file(path):
    """
    Opens a file at the specified path and extracts a protein sequence from it.

    Args:
        path (str): The path to the file containing the sequence.

    Returns:
        str or None: The extracted sequence if it is valid and follows the correct format, 
                     otherwise None.

    Raises:
        FileNotFoundError: If the specified file does not exist.
        ValueError: If the file format is incorrect or the sequence contains illegal characters.
    """
    if os.path.isfile(path):
        with open(path, 'r') as f:
            lines = f.readlines()
            if lines[0].startswith(">"):
                seq = ''.join(line.strip() for line in lines if not line.startswith('>'))
                allowed = '[ACDEFGHIKLMNPQRSTUVWY]'
                if re.match(allowed, seq):
                    return seq
                else:
                    raise ValueError("There are illegal characters in the sequence")
            else:
                raise ValueError("Incorrect file format")
    else:
        raise FileNotFoundError("File does not exist")
        

### Wczytanie pliku na podstawie id.

In [3]:
def SeqByID(id):
    """
    Retrieves the protein sequence from the UniProt database based on the given id.
    
    Arguments:
    id (string): Identifier of the protein in the UniProt database.
    
    Returns:
    string: Protein sequence.
    None: If the given id does not exist.
    """
    
    try:
        baseUrl = "http://www.uniprot.org/uniprot/"
        currentUrl = baseUrl + id + ".fasta"
        response = r.get(currentUrl)  
        cData = response.text  
        
        Seq = StringIO(cData) 
        pSeq = list(SeqIO.parse(Seq, 'fasta')) 
        sequence = str(pSeq[0].seq)
        return sequence
    except: 
        print("Given id doesn't exist")
        return None

### Wygenerowanie macierzy kropkowej

In [4]:
def create_matrix(seq1, seq2):
    """
    Creates a matrix where matching positions between two sequences are marked with 1.

    Arguments:
    seq1 (str): The first input sequence.
    seq2 (str): The second input sequence.

    Returns:
    numpy.ndarray: The matrix with dimensions len(seq1) x len(seq2) where matching positions are marked with 1.

    Raises:
    ValueError: If either input sequence is empty.
    """
    
    if not seq1 or not seq2:
        raise ValueError("Input sequences cannot be empty")
    
    n = len(seq1)
    m = len(seq2)
    matrix = np.zeros((n,m))
    for i in range(n):
        for j in range(m):
            if seq1[i] == seq2[j]:
                matrix[i, j] = 1
    return matrix

### Filtrowanie macierzy kropkowej dla zadanych:
- rozmiaru okna,
- progu filtra

In [5]:
def denoising(threshold, window, matrix):
    """
    Applies denoising to a binary matrix by setting elements to zero if the sum of elements in a window along a diagonal
    is below a specified threshold.

    Arguments:
    threshold (int): The threshold value for denoising.
    window (int): The size of the window used for denoising.
    matrix (numpy.ndarray): The binary matrix to denoise.

    Returns:
    numpy.ndarray: The denoised binary matrix.

    """
    
    max_col = len(matrix[0])
    max_row = len(matrix)
    cols = [[] for _ in range(max_col)] 
    rows = [[] for _ in range(max_row)]
    diag1 = [[] for _ in range(max_row + max_col - 1)]
    diag2 = [[] for _ in range(len(diag1))]
    min_diag2 = -max_row + 1 # min wartosc dla indeksow przekatnej diag2

    for x in range(max_col):
        for y in range(max_row):
            cols[x].append(matrix[y][x])
            rows[y].append(matrix[y][x])
            diag1[x+y].append(matrix[y][x])
            diag2[x-y-min_diag2].append(matrix[y][x])
    
    #https://stackoverflow.com/questions/6313308/get-all-the-diagonals-in-a-matrix-list-of-lists-in-python

    n = len(diag2)
    for i in range(n):
        for j in range(len(diag2[i])):
            if sum(diag2[i][j:j+window]) < threshold:
                diag2[i][j]= 0
            else:
                 pass
                             
    output_matrix = np.zeros((max_row, max_col), dtype=int)
    for row_index in range(max_row):
        diagonal_index = row_index
        np.fill_diagonal(output_matrix[max_row-row_index-1:], diag2[diagonal_index]) # od ostatniego wiersza do pierwszego

    for col_index in range(1, max_col): # wypelnia nad glowna przekatna
        diagonal_index = max_row + col_index - 1  
        np.fill_diagonal(output_matrix[:, col_index:], diag2[diagonal_index])

    return output_matrix

### Wyświetlenie fitrowanej macierzy kropkowej w postaci graficznej

In [6]:
def dotplot(matrix, threshold, window):
    filename = f"dotplot_th{threshold}_w{window}.png"
    fig = px.imshow(matrix, 
                    color_continuous_scale=[[0, 'white'], [1, 'red']],
                    color_continuous_midpoint=0.5, origin='lower')  
    fig.update_layout(width=1100, height=900, title = f'Dotplot for P53 sequences of mouse and human, threshold = {threshold}, window = {window}',
                      title_x = 0.5,
                      coloraxis_colorbar=dict(outlinewidth=0, ticks=""),
                      coloraxis_showscale=False,
                      xaxis_title="P53 HUMAN", yaxis_title="P53 MOUSE",
                      xaxis_showline=True, yaxis_showline=True,
                      xaxis_linecolor='black', yaxis_linecolor='black')
    fig.update_xaxes(showticklabels=True).update_yaxes(showticklabels=True)
    fig.show()
    pio.write_image(fig, filename)


### Wywołanie stworzonych funkcji na przykładzie badanych białek - TP53 u człowieka i myszy - przykładowych pary sekwencji ewolucyjnie powiązanych

In [7]:
seq_h = SeqByID('P04637')
seq_m = SeqByID('P02340')
mat = create_matrix(seq_m, seq_h)
filtered_matrix = denoising(8, 19, mat)
fm = denoising(0,1,mat)
dotplot(fm, 0, 1)
dotplot(filtered_matrix, 6 , 18)


### Wywołanie stworzonych funkcji na przykładzie badanych białek - P53 u myszy i MDM2 u człowieka - przykładowych pary sekwencji ewolucyjnie niepowiązanych


In [8]:
def dotplot(matrix, threshold, window):
    filename = f"dotplot_th{threshold}_w{window}.png"
    fig = px.imshow(matrix, 
                    color_continuous_scale=[[0, 'white'], [1, 'red']],
                    color_continuous_midpoint=0.5, origin='lower')  
    fig.update_layout(width=1100, height=900, title = f'Dotplot for MDM2_human and P53_MOUSE sequences, threshold = {threshold}, window = {window}',
                      title_x = 0.5,
                      coloraxis_colorbar=dict(outlinewidth=0, ticks=""),
                      coloraxis_showscale=False,
                      xaxis_title="MDM2 HUMAN", yaxis_title="P53 MOUSE",
                      xaxis_showline=True, yaxis_showline=True,
                      xaxis_linecolor='black', yaxis_linecolor='black')
    fig.update_xaxes(showticklabels=True).update_yaxes(showticklabels=True)
    fig.show()
    pio.write_image(fig, filename)
    
seq_h = SeqByID('Q00987')
seq_m = SeqByID('P02340')
mat = create_matrix(seq_m, seq_h)
filtered_matrix = denoising(0, 1, mat)
dotplot(filtered_matrix, 0,1)
filtered_matrix = denoising(7, 25, mat)
dotplot(filtered_matrix, 3 , 10)
